Global variant を定義して、その variant 列を使って overlap filtering を試みる。

In [1]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'
from IPython.display import display
import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.io as pio
pio.templates.default = 'plotly_white'
import logging
import logzero
logzero.loglevel(logging.DEBUG)

In [2]:
dir_fname = 'work'
import os
os.chdir(dir_fname)

In [3]:
import numpy as np
from copy import copy
import pandas as pd
from BITS.clustering.seq import ClusteringSeq
from BITS.seq.align import EdlibRunner
from BITS.seq.consed import ConsedRunner
from BITS.util.io import save_pickle, load_pickle
from BITS.util.io import load_pickle, save_pickle
import numpy as np
import pandas as pd
from BITS.plot.plotly import make_hist, make_scatter, make_layout, show_plot
from BITS.clustering.seq import ClusteringSeq
import consed
from BITS.seq.align import EdlibRunner
from collections import Counter, defaultdict
from logzero import logger
from dataclasses import dataclass
from typing import List, Tuple
import random
from copy import copy
from collections import Counter
from dataclasses import dataclass
from logzero import logger
import numpy as np
from vca.types import TRUnit
from BITS.clustering.seq import ClusteringSeq
from BITS.seq.align import EdlibRunner
from BITS.util.io import load_pickle, save_pickle
from BITS.util.proc import NoDaemonPool
from BITS.seq.utils import revcomp

In [4]:
def read_to_forward_units(read):
    """Return all units contained in <read> so that starnd of every unit is same as the forward master unit."""
    return [read.seq[unit.start:unit.end] if unit.id == 0 else revcomp(read.seq[unit.start:unit.end])
            for unit in read.units]

In [5]:
sync_reads = load_pickle("centromere_reads_incl_low_cover_rate_all_sync.pkl")

In [7]:
len(sync_reads)

1905

In [8]:
sync_units = []
for read in sync_reads:
    sync_units += read_to_forward_units(read)

In [9]:
len(sync_units)

46539

In [6]:
centromere_phreds = load_pickle("centromere_phreds_incl_low_cover_rate_all_sync.pkl")

In [11]:
sync_quals = []
for read in sync_reads:
    sync_quals += [centromere_phreds[read.name][unit.start:unit.end] if unit.id == 0
                   else np.flip(centromere_phreds[read.name][unit.start:unit.end])
                   for unit in read.units]

-> この数ではクラスタリングも厳しい。

In [7]:
db_prefix = "DMEL_CSS"
db_fname = f"{db_prefix}.db"
las_fname = f"TAN.{db_prefix}.las"
from vca import ReadViewer
v = ReadViewer(db_fname, las_fname)

In [8]:
sync_reads_by_id = {read.id: read for read in sync_reads}

In [11]:
logzero.loglevel(logging.INFO)
v.show(read=sync_reads_by_id[369])
logzero.loglevel(logging.DEBUG)

[I 190924 00:38:13 log:17] Starting distance matrix calculation 
[I 190924 00:38:13 log:19] Finished distance matrix calculation


In [78]:
!(cat master_unit)

caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatagatgtaagaataactgttttgagcagctaattaccagtgctaacgatccctattactttttgaaggatttagggaaattaatttttggatcaattttcgcattttttgtaaggaggggggtcatcaaaatttgcaaaatatggccaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacattccatattcagacaattattttttatgttgtggcaaaataaatgattatttgatgaccgaaatttggaaaaacagactctg


In [9]:
master_unit = "caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatagatgtaagaataactgttttgagcagctaattaccagtgctaacgatccctattactttttgaaggatttagggaaattaatttttggatcaattttcgcattttttgtaaggaggggggtcatcaaaatttgcaaaatatggccaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacattccatattcagacaattattttttatgttgtggcaaaataaatgattatttgatgaccgaaatttggaaaaacagactctg"

In [10]:
# Variants and sequencing errors

class PairwiseAlignment:
    def __init__(self, a_seq, b_seq):
        er = EdlibRunner("global", revcomp=False, cyclic=False)
        self.fcigar = er.align(b_seq.lower(), a_seq.lower()).cigar.flatten().string   # NOTE: b vs a; be careful!
        self.source, self.target = '', ''
        s_pos, t_pos = 0, 0
        for c in self.fcigar:
            if c == '=' or c == 'X':
                self.source += a_seq[s_pos]
                self.target += b_seq[t_pos]
                s_pos += 1
                t_pos += 1
            elif c == 'I':
                self.source += '-'
                self.target += b_seq[t_pos]
                t_pos += 1
            else:
                self.source += a_seq[s_pos]
                self.target += '-'
                s_pos += 1
        
    def show(self, by_cigar=False):
        if by_cigar:   # standard alignment like BLAST
            print(self.source)
            print(self.fcigar)
            print(self.target)
        else:
            print(''.join([' ' if c == '=' else self.source[i] for i, c in enumerate(self.fcigar)]))
            print(''.join([self.source[i] if c == '=' else ' ' for i, c in enumerate(self.fcigar)]))
            print(''.join([' ' if c == '=' else self.target[i] for i, c in enumerate(self.fcigar)]))

def count_variants(cluster_cons_unit, cluster_units):
    """Given a set of unit sequences <units> in a cluster, calculate the composition of
    nucleotides including '-' (= distribution of each )
    for each position on <cluster_cons_unit> as a seed.
    from which <units> are generated, compute the variations (= nucleotides inconsistent between
    <units> and <cluster_cons_unit> and their relative frequency).
    Since a cluster should be homogeneous (i.e., mono-source), the relative frequencies are
    expected to be not much larger than sequencing error.
    """
    assert cluster_cons_unit != "", "Empty strings are not allowed"
    # TODO: how to decide "same variant?" especially for multiple variations on same position (but slightly different among units)?
    variants = Counter()
    for unit in cluster_units:
        assert unit != "", "Empty strings are not allowed"
        alignment = PairwiseAlignment(cluster_cons_unit, unit)   # alignment.fcigar(cluster_cons_unit) = unit
        tpos = 0
        var_index = 0   # positive values for continuous insertions
        for i, c in enumerate(alignment.fcigar):
            if c == '=':
                var_index = 0
            elif c == 'I':
                var_index += 1
            if c != '=':
                variants[(tpos, var_index, c, alignment.target[i])] += 1   # TODO: multiple D on the same pos are aggregated
            if c != 'I':
                tpos += 1
        assert tpos == len(cluster_cons_unit)
    return variants

def list_variations(template_unit, cluster_cons_unit):
    """Single-vs-single version of count_variants().
    That is, list up the differences between the (imaginary) template unit and the consensus unit
    of a cluster (which should be a real instance).
    The return value is [(position_on_template_unit, variant_type, base_on_cluster_cons_unit)].
    """
    assert template_unit != "" and cluster_cons_unit != "", "Empty strings are not allowed"
    return list(count_variants(template_unit, [cluster_cons_unit]).keys())

In [11]:
# Probability of alignment 1) between units and 2) between a unit and a representative unit

def phred_to_log_p_correct(phred):
    return np.log10(1 - np.power(10, -phred / 10))

def phred_to_log_p_error(phred):
    return -phred / 10

def log_prob_gen(cons_unit, obs_unit, obs_qual=None, p_non_match=0.01):
    """Log likelihood of generating <obs_unit> from <cons_unit>.
    <obs_qual> is positional QVs of <obs_unit> and if not given,
    <p_non_match> is used as average error rate for every position.
    """
    if cons_unit == "":   # input sequences for <cons_unit> were empty; or, Consed did not return
        return -np.inf

    # Compute alignment
    er = EdlibRunner("global", revcomp=False)
    fcigar = er.align(cons_unit, obs_unit).cigar.flatten().string
    #logger.debug(fcigar)
    
    # Calculate the sum of log probabilities for each position in the alignment
    if obs_qual is None:
        n_match = Counter(fcigar)['=']
        n_non_match = len(fcigar) - n_match
        return n_match * np.log10(1 - p_non_match) + n_non_match * np.log10(p_non_match)
    else:
        p = 0.
        pos = 0
        for c in fcigar:
            p += (phred_to_log_p_correct(obs_qual[pos]) if c == '='
                  else phred_to_log_p_error(obs_qual[pos]))
            if c in ('=', 'X', 'D'):
                pos += 1
        assert pos == len(obs_unit) == len(obs_qual), "Invalid length"
        return p

def log_prob_align(unit_x, unit_y, qual_x=None, qual_y=None, p_error=0.01):
    """Log likelihood of alignment between <unit_x> from <unit_y>.
    <qual_*> is positional QVs of <unit_*> and if not given,
    <p_error> is used as average error rate for every position of each read.
    """
    # Compute alignment
    er = EdlibRunner("global", revcomp=False)
    fcigar = er.align(unit_x, unit_y).cigar.flatten().string
    #logger.debug(fcigar)
    
    # Calculate the sum of log probabilities for each position in the alignment
    if qual_x is None and qual_y is None:
        p_match = (1 - p_error) * (1 - p_error)
        n_match = Counter(fcigar)['=']
        n_non_match = len(fcigar) - n_match
        return n_match * np.log10(p_match) + n_non_match * np.log10(1 - p_match)
    else:
        p = 0.
        pos_x = pos_y = 0
        for c in fcigar:   # fcigar(unit_y) = unit_x
            p_match = phred_to_log_p_correct(qual_x[pos_x]) + phred_to_log_p_correct(qual_y[pos_y])
            p += (p_match if c == '='
                  else np.log10(1 - np.power(10, p_match)))
            if c in ('=', 'X', 'I'):
                pos_x += 1
            if c in ('=', 'X', 'D'):
                pos_y += 1
        assert pos_x == len(unit_x) == len(qual_x) and pos_y == len(unit_y) == len(qual_y), "Invalid length"
        return p
    
def log_factorial(n):
    return np.sum([np.log10(i) for i in range(1, n + 1)])
    
def log_prob_composition(cons_unit, obs_units, p_error=0.001):   # TODO: use positional QVs
    """Log likelihood of composition of <obs_units> given <cons_unit> as a seed; i.e., probability of alignment pileup.
    <p_error> is used for average sequencing error rate (= non-match rate in a single alignment).
    Concretely, compute Multinomial(n_A, ..., n_-; p_A, ..., p_-) for each position, where p_X = 1 - p_error
    if X is the base of <cons_unit>, otherwise p_X = p_error.
    """
    var_counts = count_variants(cons_unit, obs_units)
    var_pos = [pos for pos, index, op, base in var_counts.keys()]
    
    # compute for matches
    n_matches = len(cons_unit) - len(set(var_pos))
    p_match = n_matches * len(obs_units) * np.log10(1 - p_error)
    
    # compute for variants
    var_freqs = defaultdict(Counter)   # {(pos, index): Counter('A': n_A, ..., '-': n_-)} for each variant column
    for (pos, index, op, base), count in var_counts.items():   # list up frequencies of each variant for each position
        var_freqs[(pos, index)][base] = count
    log_factorial_N = log_factorial(len(obs_units))
    p_var = 0.
    for key, counts in var_freqs.items():   # for each variant position
        p_var += log_factorial_N
        for base, count in counts.items():
            p_var -= log_factorial(count)
            p_var += count * np.log10(p_error)
        n_match = len(obs_units) - np.sum(list(counts.values()))   # number of units having base same as seed
        p_var -= log_factorial(n_match)
        p_var += n_match * np.log10(1 - p_error)

    return p_match + p_var

In [12]:
def normalize_assignments(assignments):
    """Convert a clustering state <assignments> so that all essentially equal states can be
    same array. Return value type is Tuple so that it can be hashed as a dict key.
    """
    convert_table = {}
    new_id = 0
    for cluster_id in assignments:
        if cluster_id not in convert_table:
            convert_table[cluster_id] = new_id
            new_id += 1
    return tuple([convert_table[cluster_id] for cluster_id in assignments])

@dataclass(eq=False)
class SplitMergeClustering:
    units: List[str]
    quals: np.ndarray
    alpha: float
    
    def __post_init__(self):
        self.N = len(self.units)   # number of data
        self.assignments = np.zeros([self.N], dtype=np.int16)   # cluster assignments

        # Compute all-vs-all unit alignment likelihood
        #self.log_p_mat = np.zeros([self.N, self.N], dtype=np.float32)
        #for i in range(self.N):
        #    for j in range(i + 1, self.N):
        #        self.log_p_mat[i][j] = self.log_p_mat[j][i] = log_prob_align(self.units[i], self.units[j],
        #                                                                    self.quals[i], self.quals[j])
        
        # Cache for values computationally expensive
        self.cache_log_prob_clustering = {}   # {normalized_assignments: probability}
        self.cache_cluster_cons = {}   # {unit_ids: cluster_cons}
        
        # Pre-compute some constants
        self.const_ewens = -np.sum([np.log10(self.alpha + i) for i in range(self.N)])
        self.const_gibbs = -np.log10(self.N - 1 + self.alpha)
        
        # Compute consensus unit of the whole units so that comparing clusters can be easy
        self.template_unit = self.cluster_cons(0)
        
    def show_clustering(self):
        er = EdlibRunner("global", revcomp=False)
        for cluster_id in np.unique(self.assignments):
            print(f"Cluster {cluster_id} ({len(self.cluster_units(cluster_id))} units):\n"
                  f"{self.cluster_unit_ids(cluster_id)}\n"
                  f"{self.cluster_cons(cluster_id)}\n"
                  f"{er.align(self.cluster_cons(cluster_id), self.template_unit).cigar.flatten().string}")
            print("---")
            for unit in self.cluster_units(cluster_id):
                print(f"{er.align(unit, self.cluster_cons(cluster_id)).cigar.flatten().string}")
                
    def n_units(self, cluster_id, assignments=None, exclude_unit=None):
        """Return the number of units in the cluster <cluster_id> given a clustering state <assignments>,
        while excluding a unit <exclude_unit> if provided."""
        return len(self.cluster_unit_ids(cluster_id, assignments, exclude_unit))
            
    def cluster_unit_ids(self, cluster_id, assignments=None, exclude_unit=None):
        """Return indices of the units belonging to the cluster <cluster_id> given a clustering state <assignments>,
        while excluding a unit <exclude_unit> if provided."""
        return [i for i in range(self.N)
                if i != exclude_unit and (self.assignments if assignments is None else assignments)[i] == cluster_id]

    def cluster_units(self, cluster_id, assignments=None, exclude_unit=None):
        """Return unit sequences belonging to the cluster <cluster_id> given a clustering state <assignments>,
        while excluding a unit <exclude_unit> if provided."""
        return [self.units[i] for i in self.cluster_unit_ids(cluster_id, assignments, exclude_unit)]
    
    def n_clusters(self, assignments=None):
        """Return the number of clusters."""
        return len(self.cluster_ids(self.assignments if assignments is None else assignments))

    def cluster_ids(self, assignments=None):
        """Return a list of cluster indices."""
        return np.unique(self.assignments if assignments is None else assignments)

    def cluster_cons(self, cluster_id, assignments=None, exclude_unit=None):
        """Return the consensus sequence of the units belonging to the cluster <cluster_id> given a clustering state <assignments>,
        while excluding a unit <exclude_unit> if provided."""
        # Check the cache
        cluster_units = set(self.cluster_units(cluster_id, assignments))
        excluded = False
        if exclude_unit is None or exclude_unit not in cluster_units:
            if tuple(sorted(cluster_units)) in self.cache_cluster_cons:
                return self.cache_cluster_cons[tuple(sorted(cluster_units))]
        else:
            cluster_units.remove(exclude_unit)
            excluded = True
        cluster_units = sorted(cluster_units)
        
        #cluster_units = self.cluster_units(cluster_id, assignments, exclude_unit)   # units belonging to the cluster
        if len(cluster_units) == 0:   # cluster with single unit which is excluded
            cons = ""
        elif len(cluster_units) == 1:   # cluster with single unit
            cons = cluster_units[0]   # TODO: NOTE: single data cluster can be harmful!
        else:
            cons = consed.consensus(cluster_units)
        
        if not excluded:
            self.cache_cluster_cons[tuple(cluster_units)] = cons
        return cons
        
    def log_prob_ewens(self, assignments=None):
        """Return the probability of partition."""
        p = self.n_clusters() * np.log10(self.alpha)
        for cluster_id in self.cluster_ids(assignments):
            p += log_factorial(self.n_units(cluster_id, assignments) - 1)
        return p + self.const_ewens
    
    def log_prob_cluster_composition(self, cluster_id, assignments=None, p_error=0.001):
        """Return log probability of the composition of the cluster <cluster_id> given a clustering state <assignments>"""
        return log_prob_composition(self.cluster_cons(cluster_id, assignments),
                                    self.cluster_units(cluster_id, assignments))

    def log_prob_units_generation(self, cluster_id, assignments=None):
        """Return log probability of generating the units belonging to a cluster <cluster_id> from the cluster
        given a clustering state <assignments>."""
        cons = self.cluster_cons(cluster_id, assignments)
        return np.sum([log_prob_gen(cons, unit) for unit in self.cluster_units(cluster_id, assignments)])
        
    def log_prob_clustering(self, assignments=None):
        """Compute the joint probability of the current clustering state."""
        # Check the cache
        normalized_assignments = normalize_assignments(self.assignments if assignments is None else assignments)
        if normalized_assignments in self.cache_log_prob_clustering:
            logger.debug(f"Found in cache")
            return self.cache_log_prob_clustering[normalized_assignments]
        
        # First of all, check if consensus sequence exists for every cluster
        for cluster_id in self.cluster_ids(assignments):
            cons = self.cluster_cons(cluster_id, assignments)
            if cons == "":   # Consed did not return
                return -np.inf

        p_ewens = self.log_prob_ewens(assignments)
        p_cluster_compositions = np.sum([self.log_prob_cluster_composition(cluster_id, assignments)
                                         for cluster_id in self.cluster_ids(assignments)])
        p_gen_units = np.sum([self.log_prob_units_generation(cluster_id, assignments)
                              for cluster_id in self.cluster_ids(assignments)])

        p = p_ewens + p_cluster_compositions + p_gen_units
        self.cache_log_prob_clustering[normalized_assignments] = p
        return p
        
    def gibbs_sampling_single(self, unit_id, cluster_ids, assignments):
        """Compute probability of the unit assignment for each cluster while excluding the unit."""
        # NOTE: here assignment to a new cluster is not considered because of its very low probability
        #weights = tuple(map(lambda log_p: np.power(10, log_p),
        #                    [(np.log10(self.n_units(cluster_id, assignments, exclude_unit=unit_id))
        #                      - np.log10(self.N - 1 + self.alpha)
        #                      + log_prob_gen(self.cluster_cons(cluster_id, assignments, exclude_unit=unit_id),
        #                                  self.units[unit_id]))
        #                     for cluster_id in cluster_ids]))
        #new_assignment = random.choices(cluster_ids, weights=weights)[0]   # sample a new cluster assignment based on the probabilities
        #logger.debug(f"weights: {weights}, {assignments[unit_id]} -> {new_assignment}")
        #return new_assignment
        
        # NOTE: below is a proxy of Gibbs sampling; deterministically decide the nearest cluster as assignment
        max_prob = 0.
        max_cluster_id = -1
        for cluster_id in cluster_ids:
            log_p = (np.log10(self.n_units(cluster_id, assignments, exclude_unit=unit_id))
                     + self.const_gibbs
                     + log_prob_gen(self.cluster_cons(cluster_id, assignments, exclude_unit=unit_id),
                                    self.units[unit_id]))
            p = np.power(10, log_p)
            if p > max_prob:
                max_prob = p
                max_cluster_id = cluster_id
        return max_cluster_id

    def gibbs_sampling(self, unit_ids, cluster_ids, assignments, n_iter=1):
        """Re-assign each unit of <unit_ids> into one of the clusters <cluster_ids>,
        Given a clustering state <assignments>.
        """
        for t in range(n_iter):
            logger.debug(f"Round {t}")
            for unit_id in unit_ids:
                #logger.debug(assignments)
                old_assignment = assignments[unit_id]
                assignments[unit_id] = self.gibbs_sampling_single(unit_id, cluster_ids, assignments)
                new_assignment = assignments[unit_id]
                logger.debug(f"Unit {unit_id}: {old_assignment} -> {new_assignment}")
        return assignments
    
    def do_gibbs(self, n_iter=2):
        """Run a single iteration of Gibbs sampling with all units."""
        p_old = self.log_prob_clustering()
        self.assignments = self.gibbs_sampling(list(range(self.N)), self.cluster_ids(), self.assignments, n_iter)
        p_new = self.log_prob_clustering()
        logger.debug(f"State prob: {p_old} -> {p_new}")
        logger.debug(self.assignments)
    
    def do_proposal(self, n_iter=30):
        """Propose a new state by choosing random two units."""
        for t in range(n_iter):
            x, y = random.sample(list(range(self.N)), 2)
            logger.debug(f"Selected: {x}({self.assignments[x]}) and {y}({self.assignments[y]})")
            if self.assignments[x] == self.assignments[y]:
                logger.debug("Split")
                self.propose_split(x, y)
            else:
                logger.debug("Merge")
                self.propose_merge(x, y)

    def propose_split(self, x, y, n_gibbs_iter=2):
        # Split cluster <old_cluster_id> into <old_cluster_id> and <new_cluster_id>
        old_cluster_id = self.assignments[x]
        new_cluster_id = np.max(self.assignments) + 1
        new_assignments = np.copy(self.assignments)
        
        # Assign each unit to one of x and y randomly   # TODO: random assignment or nearest?
        new_assignments[y] = new_cluster_id
        for i in range(self.N):
            if i != x and i != y and new_assignments[i] == old_cluster_id:
                new_assignments[i] = random.choice((old_cluster_id, new_cluster_id))
                #if self.log_p_mat[i][x] < self.log_p_mat[i][y]:
                #    new_assignments[i] = new_cluster_id
        logger.debug(f"\nCurrent state:\n{self.assignments}\nProposed state (init):\n{new_assignments}")
        
        # Re-assign each unit to one of the new clusters (= Gibbs sampling)
        self.gibbs_sampling(self.cluster_unit_ids(old_cluster_id),
                            (old_cluster_id, new_cluster_id),
                            new_assignments, n_iter=n_gibbs_iter)
        logger.debug(f"\nCurrent state:\n{self.assignments}\nProposed state (Gibbs):\n{new_assignments}")
        
        # Compare the probability of the current state and the proposed state
        p_current = self.log_prob_clustering()
        p_new = self.log_prob_clustering(new_assignments)
        logger.debug(f"Current state prob: {p_current}, Proposed state prob: {p_new}")
        if p_current < p_new:
            logger.debug("Accepted")
            self.assignments = new_assignments
        else:
            logger.debug("Rejected")
            
    def propose_merge(self, x, y):
        # Merge two clusters if the consensus sequences are same   # TODO: allow some diff when noise exists?
        if self.cluster_cons(self.assignments[x]) == self.cluster_cons(self.assignments[y]):
            logger.debug("Accepted")
            for i in range(self.N):
                if self.assignments[i] == old_cluster_id_y:
                    self.assignments[i] = old_cluster_id_x
        else:
            logger.debug("Rejected")
        
        """
        # Merge cluster <old_cluster_id_x> and <old_cluster_id_y> into <old_cluster_id_x>
        old_cluster_id_x = self.assignments[x]
        old_cluster_id_y = self.assignments[y]
        new_assignments = np.copy(self.assignments)
        
        # Change cluster assignment of the units in the cluster which units[y] belongs to
        for i in range(self.N):
            if new_assignments[i] == old_cluster_id_y:
                new_assignments[i] = old_cluster_id_x
        logger.debug(f"\nCurrent state:\n{self.assignments}\nProposed state:\n{new_assignments}")
        
        # Compare the probability of the current state and the proposed state
        p_current = self.log_prob_clustering()
        p_new = self.log_prob_clustering(new_assignments)
        logger.debug(f"Current state prob: {p_current}, Proposed state prob: {p_new}")
        if p_current < p_new:
            logger.debug("Accepted")
            self.assignments = new_assignments
        else:
            logger.debug("Rejected")
        """

In [18]:
def reads_to_smc_inputs(reads):
    # units/quals = [read1_unit1, read1_unit2, ..., read1_unitN, read2_unit1, ..., read_L_unit_M]
    units = [unit for read in reads for unit in read_to_forward_units(read)]
    quals = []
    for read in reads:
        quals += [centromere_phreds[read.name][unit.start:unit.end] if unit.id == 0   # forward against master unit
                  else np.flip(centromere_phreds[read.name][unit.start:unit.end])   # revcomp
                  for unit in read.units]
    return (units, quals)

def smc_outputs_to_reads(smc_output, reads):
    ret_reads = []
    acc = 0
    for i, read in enumerate(reads):
        ret_read = copy(read)
        assignments = smc.assignments[acc:acc + len(read.units)]
        for j, unit in enumerate(ret_read.units):
            unit.id = assignments[j]
        ret_reads.append(read)
        acc += len(read.units)
    return ret_reads

In [256]:
# k-global variant vectors
reads = [sync_reads_by_id[read_id] for read_id in (73, 7556, 90327, 99318, 198167, 381787)]

In [19]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (73, 16873, 90327, 198167, 211431, 317383, 381787)]

In [21]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

In [44]:
smc.do_proposal(100)
smc.do_gibbs()

[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:197] Selected: 25(31) and 41(17)
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:197] Selected: 67(8) and 41(17)
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:197] Selected: 136(30) and 23(18)
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:197] Selected: 94(18) and 71(18)
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:199] Split
[D 190921 00:39:51 <ipython-input-17-a23e5296b461>:218] 
    Current state:
    [15 10 32 27 29 36 25 25  4 32 20 23 30 15 10 17 27 29 32 27 29 30 32 18
     29 31 33 12 13 18 29 31 33 13 25 34  3 24 14 28 32 17  7 23 34 

[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 171(31) and 40(32)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 65(18) and 94(37)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 231(36) and 76(31)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 16(27) and 118(27)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:199] Split
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:218] 
    Current state:
    [15 10 32 27 29 36 25 25  4 32 20 23 30 15 10 17 27 29 32 27 29 30 32 37
     29 31 33 12 13 18 29 31 33 13 25 34  3 24 14 28 32 17  7 23 

[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 12: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 21: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 93: 38 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 103: 38 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 114: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 127: 38 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 136: 38 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 144: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 154: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:176] Round 1
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 12: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:182] Unit 21: 30 -> 30
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:1

[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 141(37) and 223(14)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 217(28) and 210(29)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 148(16) and 11(23)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:197] Selected: 126(23) and 183(33)
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 00:39:52 <ip

[D 190921 00:39:52 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 35: 34 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 44: 38 -> 38
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 51: 38 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 59: 34 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 177: 34 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 190: 38 -> 38
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 197: 38 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 205: 34 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 222: 38 -> 38
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 229: 34 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:182] Unit 237: 38 -> 34
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:176] Round 1
[D 190921 00:39:53 <ipython-input-17-a23e5296b461>:

...

[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 208: 33 -> 33
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 209: 31 -> 31
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 210: 29 -> 29
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 211: 18 -> 18
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 212: 14 -> 14
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 213: 8 -> 8
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 214: 0 -> 0
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 215: 33 -> 33
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 216: 14 -> 14
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 217: 28 -> 28
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 218: 40 -> 40
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 219: 17 -> 17
[D 190921 00:39:58 <ipython-input-17-a23e5296b461>:182] Unit 220: 7 -> 7
[D 190921 00:39:58 <ipython-inp

[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 73: 21 -> 21
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 74: 27 -> 27
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 75: 29 -> 29
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 76: 31 -> 31
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 77: 31 -> 31
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 78: 2 -> 2
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 79: 12 -> 12
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 80: 16 -> 16
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 81: 32 -> 32
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 82: 20 -> 20
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 83: 22 -> 22
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 84: 26 -> 26
[D 190921 00:40:00 <ipython-input-17-a23e5296b461>:182] Unit 85: 29 -> 29
[D 190921 00:40:00 <ipython-input-17-a23

[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 183: 33 -> 33
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 184: 14 -> 14
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 185: 28 -> 28
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 186: 40 -> 40
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 187: 17 -> 17
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 188: 7 -> 7
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 189: 23 -> 23
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 190: 38 -> 38
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 191: 14 -> 14
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 192: 28 -> 28
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 193: 40 -> 40
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 194: 17 -> 17
[D 190921 00:40:02 <ipython-input-17-a23e5296b461>:182] Unit 195: 7 -> 7
[D 190921 00:40:02 <ipython-i

[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 48: 17 -> 17
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 49: 7 -> 7
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 50: 23 -> 23
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 51: 34 -> 34
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 52: 8 -> 8
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 53: 36 -> 36
[D 190921 00:40:03 <ipython-input-17-a23e5296b461>:182] Unit 54: 33 -> 33
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 55: 5 -> 5
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 56: 1 -> 1
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 57: 29 -> 29
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 58: 3 -> 3
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 59: 34 -> 34
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>:182] Unit 60: 8 -> 8
[D 190921 00:40:04 <ipython-input-17-a23e5296b461>

[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 159: 12 -> 12
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 160: 2 -> 2
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 161: 31 -> 31
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 162: 29 -> 29
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 163: 26 -> 26
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 164: 22 -> 22
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 165: 20 -> 20
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 166: 32 -> 32
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 167: 16 -> 16
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 168: 12 -> 12
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 169: 2 -> 2
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 170: 31 -> 31
[D 190921 00:40:05 <ipython-input-17-a23e5296b461>:182] Unit 171: 31 -> 31
[D 190921 00:40:05 <ipython-i

In [46]:
labeled_reads = smc_outputs_to_reads(smc, reads)

In [192]:
import matplotlib.cm as cm
from matplotlib.colors import rgb2hex, XKCD_COLORS
from BITS.plot.plotly import make_line, make_rect, make_scatter, make_layout, show_plot

def show_labeled_read(read, max_read_len):
    shapes = [make_line(0, 0, read.length, 0, "grey", 3, 'above')]
    traces = []
    id_to_col = {}
    for i, col in enumerate(XKCD_COLORS.values()):   # NOTE: up to ~1000 cols
        id_to_col[i] = col
    shapes += [make_line(unit.start, 0, unit.end, 0, id_to_col[unit.id], 5, 'above')
               for i, unit in enumerate(read.units)]
    trace_unit = make_scatter([unit.start for i, unit in enumerate(read.units)],
                              [0 for unit in read.units],
                              text=[unit.id for unit in read.units],
                              text_pos="top right", text_size=10, text_col="black", mode="text",
                              name="TR unit",
                              show_legend=False)
    trace_info = make_scatter([unit.start for i, unit in enumerate(read.units)],
                              [0 for unit in read.units],
                              text=[f"unit {i} (id={unit.id if read.synchronized else ''})<br>"
                                    f"[{unit.start}:{unit.end}] ({unit.length} bp)"
                                    for i, unit in enumerate(read.units)],
                              col=[id_to_col[unit.id] for unit in read.units],
                              show_legend=False)
    traces += [trace_unit, trace_info]

    # Show plot
    layout = make_layout(height=200, title=f"{read.id}", x_range=(-0.01 * max_read_len, max_read_len * 1.01),
                         x_grid=False, y_grid=False, shapes=shapes)
    show_plot(traces, layout)

In [97]:
for read in labeled_reads:
    show_labeled_read(read, max_n_units=max([len(read.units) for read in labeled_reads]))

オーバーラップは strand が違う場合はユニット列をひっくり返す必要があることに注意

In [98]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (236, 369, 87619, 191931)]

In [99]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

In [110]:
smc.do_proposal(100)
smc.do_gibbs()

[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:197] Selected: 68(2) and 46(7)
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:197] Selected: 56(12) and 3(4)
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:197] Selected: 49(8) and 20(10)
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:197] Selected: 1(1) and 35(3)
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:197] Selected: 36(8) and 33(11)
[D 190921 01:36:51 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:51 

[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:125] Found in cache
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:125] Found in cache
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:229] Current state prob: -883.3896354160004, Proposed state prob: -883.3896354160004
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:234] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 49(8) and 6(3)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 47(2) and 8(1)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 68(2) and 78(8)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-inpu

[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 13(10) and 49(8)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 49(8) and 29(12)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 46(7) and 22(12)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 77(3) and 3(4)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:197] Selected: 29(12) and 70(8)
[D 190921 01:36:52 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:5

[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 71: 12 -> 12
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 82: 12 -> 12
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:224] 
    Current state:
    [11  1  2  4 12  4  3 11  1  2  8 12 13 10  2  4 11  3  8  2 10 13 12  8
      2  1 11  3  8 12  8  2  1 11 11  3  8  2 10 13 12  8 10  2 13 12  7  2
      3  8  2 10 13 12 10 13 12  8 10  2 13 12  7  2 10 13 12  7  2 10  8 12
      8  2  1 11 11  3  8  2 10 13 12  8 10]
    Proposed state (Gibbs):
    [11  1  2  4 12  4  3 11  1  2  8 12 13 10  2  4 11  3  8  2 10 13 12  8
      2  1 11  3  8 12  8  2  1 11 11  3  8  2 10 13 12  8 10  2 13 12  7  2
      3  8  2 10 13 12 10 13 12  8 10  2 13 12  7  2 10 13 12  7  2 10  8 12
      8  2  1 11 11  3  8  2 10 13 12  8 10]
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:125] Found in cache
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:125] Found in cache
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:229

[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 4: 12 -> 12
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 11: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 22: 12 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 29: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 40: 12 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 45: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 53: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 56: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 61: 14 -> 12
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 66: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 71: 12 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 82: 14 -> 14
[D 190921 01:36:53 <ipython-input-17-a23e5296b461

[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 01:36:53 <ipython-input-17-a23e5296b461>:182] Unit 10: 14 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 18: 14 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 23: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 28: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 30: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 36: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 41: 14 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 49: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 57: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 70: 14 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 72: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 78: 8 -> 8
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:182] Unit 83: 8 -

[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:234] Rejected
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:197] Selected: 82(12) and 20(10)
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:197] Selected: 60(13) and 79(2)
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:197] Selected: 58(10) and 11(12)
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:197] Selected: 63(2) and 80(10)
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:36:54 <ipython-input-17-a23e5296b461>:197] Selected: 56(12) and 2(2)
[D 190921 0

[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 10: 8 -> 8
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 11: 12 -> 12
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 12: 13 -> 13
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 13: 10 -> 10
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 14: 2 -> 2
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 15: 4 -> 4
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 16: 11 -> 11
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 17: 3 -> 3
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 18: 8 -> 8
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 19: 2 -> 2
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 20: 10 -> 10
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 21: 13 -> 13
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>:182] Unit 22: 12 -> 12
[D 190921 01:36:55 <ipython-input-17-a23e5296b461>

[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 37: 2 -> 2
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 38: 10 -> 10
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 39: 13 -> 13
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 40: 12 -> 12
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 41: 8 -> 8
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 42: 10 -> 10
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 43: 2 -> 2
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 44: 13 -> 13
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 45: 12 -> 12
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 46: 7 -> 7
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 47: 2 -> 2
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 48: 3 -> 3
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:182] Unit 49: 8 -> 8
[D 190921 01:36:56 <ipython-input-17-a23e5296b461>:1

In [111]:
labeled_reads = smc_outputs_to_reads(smc, reads)

In [112]:
for read in labeled_reads:
    show_labeled_read(read, max_n_units=max([len(read.units) for read in labeled_reads]))

In [113]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (300, 51150, 54493, 231958, 256607, 260016)]

In [114]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

[D 190921 01:39:23 consed:84] #recomputing=0, #warning=1


In [130]:
smc.do_proposal(100)
smc.do_gibbs()

[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:197] Selected: 163(17) and 175(33)
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:197] Selected: 59(9) and 17(16)
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:197] Selected: 150(9) and 106(26)
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:197] Selected: 19(25) and 45(6)
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:197] Selected: 139(16) and 180(16)
[D 190921 01:45:33 <ipython-input-17-a23e5296b461>:199] Split
[D 1909

[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 80: 33 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 81: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 87: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 93: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 101: 33 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 102: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 113: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 114: 33 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 117: 33 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 130: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 166: 33 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 168: 37 -> 37
[D 190921 01:45:34 <ipython-input-17-a23e5296b461>:182] Unit 175: 37 -> 37
[D 190921 01:45:34 <ipython-i

[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 78: 33 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 80: 33 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 81: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 87: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 93: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 101: 33 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 102: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 113: 33 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 114: 33 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 117: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 130: 33 -> 33
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 166: 37 -> 37
[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:182] Unit 168: 37 -> 37
[D 190921 01:45:35 <ipython-in

[D 190921 01:45:35 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 2: 36 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 27: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 30: 36 -> 36
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 62: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 71: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 74: 36 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 76: 36 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 79: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 91: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 94: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 115: 37 -> 37
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:182] Unit 118: 36 -> 36
[D 190921 01:45:36 <ipython-input-17-a23e5296b4

[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:197] Selected: 49(0) and 140(21)
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:197] Selected: 2(36) and 111(25)
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:197] Selected: 169(31) and 170(24)
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:197] Selected: 12(33) and 94(36)
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:197] Selected: 78(33) and 127(36)
[D 190921 01:45:36 <ipython-input-17-a23e5296b461>:202] Merge
[D 1909

...

[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 6: 35 -> 35
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 7: 24 -> 24
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 8: 20 -> 20
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 9: 33 -> 33
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 10: 31 -> 31
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 11: 1 -> 1
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 12: 33 -> 33
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 13: 28 -> 28
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 14: 33 -> 33
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 15: 28 -> 28
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 16: 21 -> 21
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 17: 16 -> 16
[D 190921 01:45:37 <ipython-input-17-a23e5296b461>:182] Unit 18: 26 -> 26
[D 190921 01:45:37 <ipython-input-17-a23e529

[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 118: 36 -> 36
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 119: 3 -> 3
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 120: 14 -> 14
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 121: 27 -> 27
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 122: 5 -> 5
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 123: 14 -> 14
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 124: 4 -> 4
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 125: 13 -> 13
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 126: 14 -> 14
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 127: 36 -> 36
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 128: 14 -> 14
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 129: 36 -> 36
[D 190921 01:45:39 <ipython-input-17-a23e5296b461>:182] Unit 130: 33 -> 33
[D 190921 01:45:39 <ipython-inp

[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 43: 12 -> 12
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 44: 12 -> 12
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 45: 6 -> 6
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 46: 4 -> 4
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 47: 14 -> 14
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 48: 12 -> 12
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 49: 0 -> 0
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 50: 13 -> 13
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 51: 32 -> 32
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 52: 4 -> 4
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 53: 14 -> 14
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 54: 12 -> 12
[D 190921 01:45:40 <ipython-input-17-a23e5296b461>:182] Unit 55: 0 -> 0
[D 190921 01:45:40 <ipython-input-17-a23e5296b46

[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 154: 35 -> 35
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 155: 18 -> 18
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 156: 32 -> 32
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 157: 24 -> 24
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 158: 9 -> 9
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 159: 7 -> 7
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 160: 7 -> 7
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 161: 36 -> 36
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 162: 24 -> 24
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 163: 17 -> 17
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 164: 18 -> 18
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 165: 35 -> 35
[D 190921 01:45:42 <ipython-input-17-a23e5296b461>:182] Unit 166: 33 -> 33
[D 190921 01:45:42 <ipython-inp

[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 80: 33 -> 33
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 81: 33 -> 33
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 82: 11 -> 11
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 83: 34 -> 34
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 84: 17 -> 17
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 85: 13 -> 13
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 86: 35 -> 35
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 87: 33 -> 33
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 88: 14 -> 14
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 89: 14 -> 14
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 90: 4 -> 4
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 91: 36 -> 36
[D 190921 01:45:43 <ipython-input-17-a23e5296b461>:182] Unit 92: 6 -> 6
[D 190921 01:45:43 <ipython-input-17-a23e5

In [131]:
labeled_reads = smc_outputs_to_reads(smc, reads)

In [132]:
for read in labeled_reads:
    show_labeled_read(read, max_n_units=max([len(read.units) for read in labeled_reads]))

エラー率の低いユニットのペアを見つけているだけではないのか？確かめる

In [134]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (559, 262499, 299496, 202130, 132531, 95028)]

In [135]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

In [151]:
smc.do_proposal(1000)
smc.do_gibbs()

[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 14(19) and 165(28)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 176(33) and 161(22)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 152(25) and 173(47)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 4(16) and 135(15)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 74(50) and 8(11)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190

[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:182] Unit 46: 14 -> 14
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:182] Unit 91: 14 -> 14
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:182] Unit 139: 14 -> 14
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:224] 
    Current state:
    [17 45 35 15 16 14 20  9 11 15 27 26 24  3 19 24 33 16  0  0 47 13 23 32
     15 16  0 42 29 23  6 33 15 15 15 29 23  6 33 24 26 27 31 50  9 20 14 16
     15 35 45 17 41 35 16 46 33  5  2 25 38 36 48 34 44 48 34  1 33 44 48 34
      1 32 50 13 47  0  0 16 33  7 19  3  7 26 27 15 11  9 20 14 16 21 35 45
     17 41 35 16 46 33  5  2 25 38 36 48  0 42 29 23  6 33 15 15 21 29 23 37
     33 18 37 13 47  0  0 16 33 24 19  3  7 26 27 15 11  9 20 14 16 31 35 45
     17 41 35 16 46 33  5  2 25 38 36  8 10  8 10 10 28 22 22 39 39 28 28 39
     28 22  4  4 44 47 33 19 33  6 23 33  6 18 33 37 23 29 15 15 15 33]
    Proposed state (Gibbs):
    [17 45 35 15 16 14 20  9 11 15 27 26 24  3 19 24 33 16  0 

[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:234] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 116(21) and 32(15)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 52(41) and 181(18)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:197] Selected: 114(15) and 9(15)
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:199] Split
[D 190921 05:28:43 <ipython-input-17-a23e5296b461>:218] 
    Current state:
    [17 45 35 15 16 14 20  9 11 15 27 26 24  3 19 24 33 16  0  0 47 13 23 32
     15 16  0 42 29 23  6 33 15 15 15 29 23  6 33 24 26 27 31 50  9 20 14 16
     15 35 45 17 41 35 16 46 33  5  2 25 38 36 48 34 44 48 34  1 33 44 48 34
      1 32 50 13 47  0  0 16 33  7 19  3  7 26 27 15 11  9

[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 48(15) and 71(34)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 31(33) and 153(38)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 61(36) and 117(29)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 183(37) and 114(15)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipyth

[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 161(22) and 87(15)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 52(41) and 63(34)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 72(1) and 85(26)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 64(44) and 9(15)
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:202] Merge
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:244] Rejected
[D 190921 05:28:44 <ipython-input-17-a23e5296b461>:197] Selected: 26(0) and 139(14)
[D 19092

...

[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 52: 41 -> 41
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 53: 35 -> 35
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 54: 16 -> 16
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 55: 46 -> 46
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 56: 33 -> 33
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 57: 5 -> 5
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 58: 2 -> 2
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 59: 25 -> 25
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 60: 38 -> 38
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 61: 36 -> 36
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 62: 48 -> 48
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 63: 34 -> 34
[D 190921 05:28:53 <ipython-input-17-a23e5296b461>:182] Unit 64: 44 -> 44
[D 190921 05:28:53 <ipython-input-17-a23e5

[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 163: 39 -> 39
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 164: 39 -> 39
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 165: 28 -> 28
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 166: 28 -> 28
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 167: 39 -> 39
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 168: 28 -> 28
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 169: 22 -> 22
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 170: 4 -> 4
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 171: 4 -> 4
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 172: 44 -> 44
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 173: 47 -> 47
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 174: 33 -> 33
[D 190921 05:28:55 <ipython-input-17-a23e5296b461>:182] Unit 175: 19 -> 19
[D 190921 05:28:55 <ipython-i

[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 84: 7 -> 7
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 85: 26 -> 26
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 86: 27 -> 27
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 87: 51 -> 51
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 88: 11 -> 11
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 89: 9 -> 9
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 90: 20 -> 20
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 91: 14 -> 14
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 92: 16 -> 16
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 93: 21 -> 21
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 94: 35 -> 35
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 95: 45 -> 45
[D 190921 05:28:57 <ipython-input-17-a23e5296b461>:182] Unit 96: 17 -> 17
[D 190921 05:28:57 <ipython-input-17-a23e5

[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 4: 16 -> 16
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 5: 14 -> 14
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 6: 20 -> 20
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 7: 9 -> 9
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 8: 11 -> 11
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 9: 51 -> 51
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 10: 27 -> 27
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 11: 26 -> 26
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 12: 24 -> 24
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 13: 3 -> 3
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 14: 19 -> 19
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 15: 24 -> 24
[D 190921 05:28:59 <ipython-input-17-a23e5296b461>:182] Unit 16: 33 -> 33
[D 190921 05:28:59 <ipython-input-17-a23e5296b46

[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 116: 21 -> 21
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 117: 29 -> 29
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 118: 23 -> 23
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 119: 37 -> 37
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 120: 33 -> 33
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 121: 18 -> 18
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 122: 37 -> 37
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 123: 13 -> 13
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 124: 47 -> 47
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 125: 0 -> 0
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 126: 0 -> 0
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 127: 16 -> 16
[D 190921 05:29:01 <ipython-input-17-a23e5296b461>:182] Unit 128: 33 -> 33
[D 190921 05:29:01 <ipython-i

In [152]:
labeled_reads = smc_outputs_to_reads(smc, reads)

In [153]:
for read in labeled_reads:
    show_labeled_read(read, max_n_units=max([len(read.units) for read in labeled_reads]))

In [154]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (5251, 430850, 273798, 363402, 400550, 369960, 303543, 271671, 26555, 265795, 243780, 345283, 109645, 279375, 106586, 320731, 287839, 169823, 99942, 289258, 62061, 423407)]

In [155]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

[D 190921 05:51:56 consed:84] #recomputing=1, #warning=0


In [172]:
smc.do_proposal(0)
smc.do_gibbs(2)

[D 190921 06:09:27 <ipython-input-17-a23e5296b461>:125] Found in cache
[D 190921 06:09:27 <ipython-input-17-a23e5296b461>:176] Round 0
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 0: 40 -> 40
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 1: 24 -> 24
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 2: 0 -> 0
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 3: 44 -> 44
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 4: 37 -> 37
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 5: 24 -> 24
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 6: 44 -> 44
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 7: 46 -> 46
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 8: 7 -> 7
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 9: 3 -> 3
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 10: 39 -> 39
[D 190921 06:09:28 <ipython-input-17-a23e5296b461>:182] Unit 11: 4 

[D 190921 06:09:30 <ipython-input-17-a23e5296b461>:182] Unit 110: 47 -> 47
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 111: 13 -> 13
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 112: 44 -> 44
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 113: 22 -> 22
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 114: 47 -> 47
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 115: 13 -> 13
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 116: 40 -> 40
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 117: 21 -> 21
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 118: 27 -> 27
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 119: 35 -> 35
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 120: 44 -> 44
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 121: 22 -> 22
[D 190921 06:09:31 <ipython-input-17-a23e5296b461>:182] Unit 122: 47 -> 47
[D 190921 06:09:31 <ipyth

[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 221: 41 -> 41
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 222: 0 -> 0
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 223: 41 -> 41
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 224: 0 -> 0
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 225: 4 -> 4
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 226: 31 -> 31
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 227: 14 -> 14
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 228: 0 -> 0
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 229: 37 -> 37
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 230: 4 -> 4
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 231: 0 -> 0
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 232: 41 -> 41
[D 190921 06:09:34 <ipython-input-17-a23e5296b461>:182] Unit 233: 0 -> 0
[D 190921 06:09:34 <ipython-input-17-a2

[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 332: 2 -> 2
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 333: 5 -> 5
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 334: 20 -> 20
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 335: 20 -> 20
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 336: 37 -> 37
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 337: 11 -> 11
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 338: 7 -> 7
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 339: 3 -> 3
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 340: 19 -> 19
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 341: 14 -> 14
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 342: 7 -> 7
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 343: 2 -> 2
[D 190921 06:09:37 <ipython-input-17-a23e5296b461>:182] Unit 344: 5 -> 5
[D 190921 06:09:37 <ipython-input-17-a2

[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 443: 31 -> 31
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 444: 24 -> 24
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 445: 41 -> 41
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 446: 31 -> 31
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 447: 8 -> 8
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 448: 44 -> 44
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 449: 37 -> 37
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 450: 46 -> 46
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 451: 7 -> 7
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 452: 2 -> 2
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 453: 15 -> 15
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 454: 24 -> 24
[D 190921 06:09:40 <ipython-input-17-a23e5296b461>:182] Unit 455: 37 -> 37
[D 190921 06:09:40 <ipython-inp

...

[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 270: 41 -> 41
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 271: 0 -> 0
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 272: 4 -> 4
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 273: 37 -> 37
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 274: 0 -> 0
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 275: 14 -> 14
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 276: 31 -> 31
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 277: 4 -> 4
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 278: 0 -> 0
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 279: 41 -> 41
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 280: 0 -> 0
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 281: 41 -> 41
[D 190921 06:09:55 <ipython-input-17-a23e5296b461>:182] Unit 282: 31 -> 31
[D 190921 06:09:55 <ipython-input-17-

[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 380: 2 -> 2
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 381: 5 -> 5
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 382: 20 -> 20
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 383: 0 -> 0
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 384: 4 -> 4
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 385: 31 -> 31
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 386: 44 -> 44
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 387: 11 -> 11
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 388: 0 -> 0
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 389: 44 -> 44
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 390: 11 -> 11
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 391: 7 -> 7
[D 190921 06:09:58 <ipython-input-17-a23e5296b461>:182] Unit 392: 3 -> 3
[D 190921 06:09:58 <ipython-input-17-a2

[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 491: 46 -> 46
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 492: 37 -> 37
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 493: 35 -> 35
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 494: 37 -> 37
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 495: 44 -> 44
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 496: 22 -> 22
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 497: 47 -> 47
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 498: 13 -> 13
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 499: 40 -> 40
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 500: 7 -> 7
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 501: 14 -> 14
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 502: 22 -> 22
[D 190921 06:10:01 <ipython-input-17-a23e5296b461>:182] Unit 503: 4 -> 4
[D 190921 06:10:01 <ipython-i

[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 602: 29 -> 29
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 603: 31 -> 31
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 604: 41 -> 41
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 605: 31 -> 31
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 606: 26 -> 26
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 607: 29 -> 29
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 608: 0 -> 0
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 609: 8 -> 8
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 610: 18 -> 18
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 611: 9 -> 9
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 612: 1 -> 1
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 613: 1 -> 1
[D 190921 06:10:04 <ipython-input-17-a23e5296b461>:182] Unit 614: 31 -> 31
[D 190921 06:10:04 <ipython-input-1

[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 713: 7 -> 7
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 714: 2 -> 2
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 715: 5 -> 5
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 716: 6 -> 6
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 717: 31 -> 31
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 718: 44 -> 44
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 719: 11 -> 11
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 720: 10 -> 10
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 721: 28 -> 28
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 722: 19 -> 19
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 723: 46 -> 46
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 724: 7 -> 7
[D 190921 06:10:07 <ipython-input-17-a23e5296b461>:182] Unit 725: 2 -> 2
[D 190921 06:10:07 <ipython-input-17-

In [173]:
labeled_reads = smc_outputs_to_reads(smc, reads)

In [174]:
for read in labeled_reads:
    show_labeled_read(read, max_n_units=max([len(read.units) for read in labeled_reads]))

In [179]:
smc.show_clustering()

Cluster 0 (50 units):
[2, 29, 44, 47, 52, 61, 180, 185, 204, 207, 218, 222, 224, 228, 231, 233, 237, 265, 269, 271, 274, 278, 280, 293, 296, 301, 310, 315, 383, 388, 416, 422, 430, 441, 490, 507, 520, 529, 534, 547, 565, 569, 590, 597, 608, 616, 624, 626, 630, 636]
caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatagatgtacgaatatctgttttgagcagctaattaccagtgctaacgatccctattacattttgaaggatttagggaaattaatttttggatcaatattcgcattttttgtaaggttctcattttttgtaaatttgcaaaatatggccaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacattccatattcagacaattattttttatgttgtggcaaaataaatgattttttgatgaccgaaatttggaaaaacagactctg
=====================================================================================================================X================I====================X==================XXXXXXX=XX=XXI============================================================================================================================================================================
---
========

=======================================================================================================================================================================================================D=============I===================================================================================================================================================
=======================================================================================================================================================================D================================================================================================================================================================================================
=====================================================================================================================================================================================================================================================================================

===================================X====================================================================================================================================================================================================================================================================================================I==============================
Cluster 23 (12 units):
[76, 81, 85, 148, 153, 157, 663, 668, 672, 696, 701, 705]
caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatcgatgtacgaatatctgttttgagcagctaattaccagtgctaacgatccctattacattttgaaggatttagggaaattaatttttgaatcaattttcgcattttttgtaagtagaagggtcatcaaaatttgcaaaatatggtcaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacatttcatattcagacaattattttttatgttgtggcaaaataaatgattacttgatgaccgaaatttggaaaaaaagactctg
============================================================X========================================================X================I=============X========================X==XX=====================

============================================================X=============================================================X=====X====================================================I============================================================================================================I========================================I==============================
==============================================================================================================================================================================================================================I=====D===================================================================================================================================
============================================================================================================================================================================================================X=======================================================================

=================================================================================================================================================================================================================================================================================================================================================================X======
=========================================================================================================================================================================================D=====================================================D=================================================================================================================X======
=====================================================================================================================================================================================================================================================================X=============X==

In [180]:
# daligner
reads = [sync_reads_by_id[read_id] for read_id in (81028, 140005, 80008, 224973, 259917, 308052, 242969, 404287)]

In [181]:
smc = SplitMergeClustering(*reads_to_smc_inputs(reads), alpha=1)

In [189]:
smc.do_proposal(0)
smc.do_gibbs(2)

[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:125] Found in cache
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:176] Round 0
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 0: 15 -> 15
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 1: 20 -> 20
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 2: 18 -> 18
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 3: 36 -> 36
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 4: 0 -> 0
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 5: 26 -> 26
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 6: 30 -> 30
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 7: 8 -> 8
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 8: 3 -> 3
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 9: 6 -> 6
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182] Unit 10: 26 -> 26
[D 190921 18:16:00 <ipython-input-170-e46b3b9e0cc5>:182]

[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 109: 3 -> 3
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 110: 6 -> 6
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 111: 26 -> 26
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 112: 24 -> 24
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 113: 19 -> 19
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 114: 30 -> 30
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 115: 8 -> 8
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 116: 3 -> 3
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 117: 16 -> 16
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 118: 27 -> 27
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 119: 4 -> 4
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 120: 32 -> 32
[D 190921 18:16:01 <ipython-input-170-e46b3b9e0cc5>:182] Unit 121: 11 -> 11
[D 190921 18:16:01 <ip

[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 49: 35 -> 35
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 50: 26 -> 26
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 51: 24 -> 24
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 52: 19 -> 19
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 53: 30 -> 30
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 54: 8 -> 8
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 55: 3 -> 3
[D 190921 18:16:02 <ipython-input-170-e46b3b9e0cc5>:182] Unit 56: 16 -> 16
[D 190921 18:16:03 <ipython-input-170-e46b3b9e0cc5>:182] Unit 57: 27 -> 27
[D 190921 18:16:03 <ipython-input-170-e46b3b9e0cc5>:182] Unit 58: 4 -> 4
[D 190921 18:16:03 <ipython-input-170-e46b3b9e0cc5>:182] Unit 59: 32 -> 32
[D 190921 18:16:03 <ipython-input-170-e46b3b9e0cc5>:182] Unit 60: 11 -> 11
[D 190921 18:16:03 <ipython-input-170-e46b3b9e0cc5>:182] Unit 61: 32 -> 32
[D 190921 18:16:03 <ipython-inp

[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 159: 3 -> 3
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 160: 8 -> 8
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 161: 30 -> 30
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 162: 37 -> 37
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 163: 0 -> 0
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 164: 13 -> 13
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 165: 18 -> 18
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 166: 20 -> 20
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 167: 15 -> 15
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:182] Unit 168: 27 -> 27
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:125] Found in cache
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:190] State prob: -2096.834931679603 -> -2096.834931679603
[D 190921 18:16:04 <ipython-input-170-e46b3b9e0cc5>:191] [15 20 

In [194]:
labeled_reads = smc_outputs_to_reads(smc, reads)
for read in labeled_reads:
    show_labeled_read(read, max([read.length for read in labeled_reads]))

In [199]:
v.show(293747)

[D 190922 18:11:30 find_units:90] inners: {SelfAlignment(ab=365, ae=3064, bb=4, be=2704), SelfAlignment(ab=10402, ae=12570, bb=10041, be=12209), SelfAlignment(ab=3236, ae=10237, bb=2876, be=9878)}


In [204]:
EdlibRunner("glocal", revcomp=True).align(master_unit, sync_reads_by_id[293747].seq)

q[None:None] vs t[5470:5827]   (364 bp, 11.3% diff)

master unit から遠すぎて encode されなかったリード